### I) XỬ LÝ DỮ LIỆU TRẬN ĐẤU ĐƯỢC RÚT TRÍCH TỪ API VÀ LƯU TRỮ VÀO DATAFRAME

In [1]:
import requests
import json
import pandas as pd
import os 
import glob
import numpy as np
import csv

#### hàm get_all_json đọc tất cả các file json của từng người chơi và lưu vào biến all_players

path_to_json: lấy đường dẫn của từng người chơi trong từng server

json_files: lấy ra 20 file json của người chơi

vòng for để lưu từng file json vào biến data dưới dạng mảng

In [37]:
def get_all_json(player, region):
    data = []
    path_to_json = '../Data_Match/' + region + '/'+player+'/'
    path_to_json = path_to_json.to_string()
    path_to_json = path_to_json[path_to_json.find(".."):len(path_to_json)]

    json_files = [pos_json for pos_json in os.listdir(path_to_json) if pos_json.endswith('.json')]
    for i in range(len(json_files)):
        f = open(path_to_json + json_files[i], "r")
        data.append(json.loads(f.read()))
        f.close()
    return data

hàm apply để chạy duyệt từng tên trong 2 server NA và KR

In [38]:
df = pd.read_csv('../Data/data_summoner_tft_csv.csv')
kr = df['kr'][:100]
na = df['na'][:100]

kr_temp = kr.to_frame()
na_temp = na.to_frame()
all_players_kr = kr_temp.apply(get_all_json, args = ("KR",), axis = 1)
all_players_na = na_temp.apply(get_all_json, args = ("NA1",), axis = 1)


In [39]:
all_players = (all_players_kr.append(all_players_na, ignore_index= True))

all_players chứa tất cả dữ liệu(dưới dạng JSON) về người chơi đó. 

thông tin của 1 trận đấu dưới dạng JSON

In [68]:
all_players[0][0]

{'metadata': {'data_version': '5',
  'match_id': 'KR_6267320509',
  'participants': ['_NjJNkxpeKQ-po15A8N1GVKYqYTAjiN1WoqkVUGfwmpHqg-yZrq6ILTUTObYOlvzsfqeuNkR1NkXVA',
   'WgAZ0CQHGmDf8yctPx5SXkU-rt-9HWv758OmfE6t_Wod8XU3k4M2_PfGrIICL7OMDXcpV-tfHrJM5Q',
   'WO7vH445Mvh-59sDpk4OAtffIxLMrm2R4wsrGT5ZcUb7cN4PDlQhDgzF0YaA5_hoL4R51IP5vDgB1Q',
   'LjGpzsuqxxKX_8HDCyOmX5bBgwC-p59Oj7rTLhaSwOgN7Uq2Py06bmYE-GE6fYFtMqc5SSc-HGr_xA',
   'XdejWcFYkQS2jJwSPR2FXlv_IZuw1txCPOLZJtUkqyusTne88RNKMgkcqKshr0clIIT4pCaNlvXwsg',
   'CtB6YjZTon2Z-pYgNfubDLUKwxAZoBQcZVQ12LyNanULi3xpFBAUPkL0yp5tdj35JDuXdYuJRPswaQ',
   'y6gI4h6o614IhVvGBBp45jA-XhRHxqx2tleVdE0egluOSK1BEM8zHVQtjqEJ5xzRvGnzqJy56GP75w',
   'YFHBmecEZcAKDUkoNKCvM_--z5qekvafrDJzBgqJFz6l5aRuEIq5_RZg2XnR_sAQ4-48ZmknJPcwXA']},
 'info': {'game_datetime': 1671450521734,
  'game_length': 2033.802001953125,
  'game_version': 'Version 12.23.483.5208 (Dec 05 2022/14:03:09) [PUBLIC] <Releases/12.23>',
  'participants': [{'augments': ['TFT7_Augment_Preparation',
    

#### lấy lõi nâng cấp của từng người chơi trong 1 game đó

##### augments: gồm 1 mảng 3 chiều:

    +Chiều thứ nhất: số lượng trận đấu của từng người chơi(20)

    +Chiều thứ hai: sô lượng lõi nâng cấp của 8 người chơi
    
    +Chiều thứ ba: lõi nâng cấp của người chơi

In [40]:
augments = []
cc = []
augment = []
for player in range(len(all_players)):
    for match in range(len(all_players[0])):
        for each_player in range(8):
            augment.append(all_players[player][match]['info']['participants'][each_player]['augments'])
        
        temp = augment.copy()
        cc.append(temp)
        augment.clear()
        
    test = cc.copy()
    augments.append(test)
    cc.clear()

trận đấu thứ nhất và lõi nâng cấp của 8 người chơi đó

In [44]:
augments[0][0]

[['TFT7_Augment_Preparation',
  'TFT8_Augment_ViCarry',
  'TFT6_Augment_JeweledLotus'],
 ['TFT8_Augment_ChannelerTrait',
  'TFT8_Augment_AnnieSupport',
  'TFT7_Augment_AxiomArc2'],
 ['TFT6_Augment_ItemGrabBag1',
  'TFT8_Augment_YuumiSupport',
  'TFT7_Augment_ScopedWeapons1'],
 ['TFT6_Augment_SecondWind1',
  'TFT8_Augment_YasuoSupport',
  'TFT6_Augment_TomeOfTraits1'],
 ['TFT6_Augment_ItemGrabBag1',
  'TFT8_Augment_YuumiSupport',
  'TFT8_Augment_PranksterEmblem'],
 ['TFT6_Augment_TinyTitans',
  'TFT8_Augment_CamilleSupport',
  'TFT6_Augment_CelestialBlessing2'],
 ['TFT6_Augment_TinyTitans',
  'TFT8_Augment_SivirSupport',
  'TFT6_Augment_PortableForge'],
 ['TFT6_Augment_ItemGrabBag1',
  'TFT8_Augment_AnnieSupport',
  'TFT6_Augment_TomeOfTraits1']]

#### lấy puuid và trận đấu của 8 người chơi

##### participants: puuid là 1 mảng 3 chiều:

    +Chiều thứ nhất: số lượng trận đấu của từng người chơi(20)
    
    +Chiều thứ hai: số lượng người chơi trong 1 trận đấu(thường là 8)

    +Chiều thứ ba: Puuid của từng người chơi
##### id_match: id là 1 mảng 2 chiều:

    +Chiều thứ nhất: số lượng trận đấu của người chơi(20)

    +Chiều thứ hai: mã trận đấu(20)

vì python không cho copy bằng cách gán biến như ta làm ở bên C++ nên phải tạo 1 biến phụ để lưu vào. Do thế code sẽ nhìn không được đẹp mắt cho lắm.

In [45]:
participants = []
id_match = []
participant = []
id = []
for player in range(len(all_players)):
    for match in range(len(all_players[0])):
        participant.append(all_players[player][match]["metadata"]["participants"])
        id.append(all_players[player][match]["metadata"]["match_id"])   

    temp1 = participant.copy()
    temp2 = id.copy()
    participants.append(temp1)
    id_match.append(temp2)
    participant.clear()
    id.clear()

Puuid của 8 người chơi trong trận đấu đầu tiên(trận 0)

In [56]:
print(participants[0][0])

['_NjJNkxpeKQ-po15A8N1GVKYqYTAjiN1WoqkVUGfwmpHqg-yZrq6ILTUTObYOlvzsfqeuNkR1NkXVA', 'WgAZ0CQHGmDf8yctPx5SXkU-rt-9HWv758OmfE6t_Wod8XU3k4M2_PfGrIICL7OMDXcpV-tfHrJM5Q', 'WO7vH445Mvh-59sDpk4OAtffIxLMrm2R4wsrGT5ZcUb7cN4PDlQhDgzF0YaA5_hoL4R51IP5vDgB1Q', 'LjGpzsuqxxKX_8HDCyOmX5bBgwC-p59Oj7rTLhaSwOgN7Uq2Py06bmYE-GE6fYFtMqc5SSc-HGr_xA', 'XdejWcFYkQS2jJwSPR2FXlv_IZuw1txCPOLZJtUkqyusTne88RNKMgkcqKshr0clIIT4pCaNlvXwsg', 'CtB6YjZTon2Z-pYgNfubDLUKwxAZoBQcZVQ12LyNanULi3xpFBAUPkL0yp5tdj35JDuXdYuJRPswaQ', 'y6gI4h6o614IhVvGBBp45jA-XhRHxqx2tleVdE0egluOSK1BEM8zHVQtjqEJ5xzRvGnzqJy56GP75w', 'YFHBmecEZcAKDUkoNKCvM_--z5qekvafrDJzBgqJFz6l5aRuEIq5_RZg2XnR_sAQ4-48ZmknJPcwXA']


mã trận đấu của người chơi đầu tiên

In [53]:
print(id_match[0])

['KR_6267320509', 'KR_6267390363', 'KR_6267598696', 'KR_6267696210', 'KR_6267766329', 'KR_6267830792', 'KR_6267978660', 'KR_6268004026', 'KR_6268008872', 'KR_6268027987', 'KR_6268029248', 'KR_6268045856', 'KR_6268047273', 'KR_6268059954', 'KR_6268063129', 'KR_6268075696', 'KR_6268097161', 'KR_6268097970', 'KR_6268121600', 'KR_6268147594']


#### lấy số lượng tộc hệ kích hoạt được(list_traits)

1 mảng 3 chiều:

    +Chiều thứ nhất: số trận đấu của từng người chơi(20)

    +Chiều thứ hai: số hệ có trong đội hình người chơi

    +Chiều thứ ba: tên hệ, số lượng và cấp của hệ đó

In [58]:
list_traits = []
in_match = []
in_player = []
for player in range(len(all_players)):
    for match in range(len(all_players[0])):
        for each_player in range(8):
            traits_each_player = all_players[player][match]['info']['participants'][each_player]['traits']
            temp = []
            for trait in range(len(traits_each_player)):
                temp.append(all_players[player][match]['info']['participants'][each_player]['traits'][trait]['name'])
                temp.append(all_players[player][match]['info']['participants'][each_player]['traits'][trait]['num_units'])
                temp.append(all_players[player][match]['info']['participants'][each_player]['traits'][trait]['tier_current'])
            
            test1 = temp.copy()
            in_player.append(test1)
            temp.clear()
        
        test2 = in_player.copy()
        in_match.append(test2)
        in_player.clear()
    
    test3 = in_match.copy()
    list_traits.append(test3)
    in_match.clear()


số lượng tộc hệ của người chơi thứ 1(trong 8) của trận đấu đầu tiên

In [62]:
print(list_traits[0][0][0])

['Set8_Aegis', 1, 0, 'Set8_Brawler', 2, 1, 'Set8_Channeler', 1, 0, 'Set8_Duelist', 1, 0, 'Set8_Heart', 2, 1, 'Set8_Mascot', 1, 0, 'Set8_Recon', 2, 1, 'Set8_StarGuardian', 1, 0, 'Set8_Supers', 3, 1, 'Set8_UndergroundThe', 3, 1]


#### danh sách các tướng có trong đội hình của từng người chơi

##### list_champions: 1 mảng 3 chiều:

    +Chiều thứ nhất: số lượng trận đấu của từng người chơi(20)

    +Chiều thứ hai: số tướng có trong đội hình người chơi

    +Chiều thứ ba: gồm tướng, số lượng đồ của tướng và bậc sao của tướng(1, 2, 3 sao)

In [64]:
list_champions = []

for player in range(len(all_players)):
    for match in range(len(all_players[0])):
        for each_player in range(8):
            temp = []
            player_champions = all_players[player][match]['info']['participants'][each_player]['units']
            for each_champion in range(len(player_champions)):
                temp.append(all_players[player][match]['info']['participants'][each_player]['units'][each_champion]['character_id'])
            test1 = temp.copy()
            in_player.append(test1)
            temp.clear()
        
        test2 = in_player.copy()
        in_match.append(test2)
        in_player.clear()
    
    test3 = in_match.copy()
    list_champions.append(test3)
    in_match.clear()

In [65]:
list_champions

[[[['TFT8_Gangplank',
    'TFT8_Vi',
    'TFT8_LeeSin',
    'TFT8_Malphite',
    'TFT8_Ezreal',
    'TFT8_Sona',
    'TFT8_Kaisa'],
   ['TFT8_Lux',
    'TFT8_Annie',
    'TFT8_Yuumi',
    'TFT8_Sona',
    'TFT8_Alistar',
    'TFT8_Ekko',
    'TFT8_Taliyah',
    'TFT8_Syndra'],
   ['TFT8_Galio',
    'TFT8_Nasus',
    'TFT8_Gangplank',
    'TFT8_LeeSin',
    'TFT8_Malphite',
    'TFT8_Yuumi',
    'TFT8_Alistar',
    'TFT8_Nunu'],
   ['TFT8_Fiora',
    'TFT8_Yasuo',
    'TFT8_Vayne',
    'TFT8_Nilah',
    'TFT8_Zoe',
    'TFT8_Leblanc',
    'TFT8_Zed',
    'TFT8_Sejuani'],
   ['TFT8_Lulu',
    'TFT8_Annie',
    'TFT8_Yuumi',
    'TFT8_Sona',
    'TFT8_Alistar',
    'TFT8_Zoe',
    'TFT8_Ekko',
    'TFT8_Soraka'],
   ['TFT8_Talon',
    'TFT8_Blitzcrank',
    'TFT8_Vi',
    'TFT8_Camille',
    'TFT8_Zoe',
    'TFT8_Leblanc',
    'TFT8_Viego',
    'TFT8_Soraka'],
   ['TFT8_Sivir',
    'TFT8_Velkoz',
    'TFT8_Chogath',
    'TFT8_Rammus',
    'TFT8_Rammus',
    'TFT8_Samira',
    'TFT8_Aureli

#### số lượng đồ mà mỗi con tướng sử dụng trong trận đấu

list_items: gồm 1 mảng 3 chiều

    +Chiều thứ nhất: số lượng trận đấu của từng người chơi(20)

    +Chiều thứ hai: số lượng người chơi trong trận đấu(8)

    +Chiều thứ ba: số lượng đồ của mỗi con tướng trong đội hình của người chơi đó

In [69]:
list_items = []

for player in range(len(all_players)):
    for match in range(len(all_players[0])):
        for each_player in range(8):
            temp = []
            player_champions = all_players[player][match]['info']['participants'][each_player]['units']
            for each_champion in range(len(player_champions)):
                temp.append(len(all_players[player][match]['info']['participants'][each_player]['units'][each_champion]['items']))
            test1 = temp.copy()
            in_player.append(test1)
            temp.clear()
        
        test2 = in_player.copy()
        in_match.append(test2)
        in_player.clear()
    
    test3 = in_match.copy()
    list_items.append(test3)
    in_match.clear()

In [74]:
list_items[0][0]

[[1, 3, 0, 2, 3, 3, 0],
 [1, 3, 1, 0, 0, 1, 3, 0],
 [1, 0, 3, 0, 0, 3, 0, 1],
 [0, 1, 1, 0, 1, 1, 3, 3],
 [0, 3, 1, 0, 1, 3, 1, 3],
 [0, 2, 0, 3, 0, 0, 1, 1],
 [0, 0, 3, 0, 3, 3, 0, 1],
 [0, 3, 1, 0, 3, 3, 1, 0]]

#### số sao của mỗi con tướng trong trận đấu

list_items: gồm 1 mảng 3 chiều

    +Chiều thứ nhất: số lượng trận đấu của từng người chơi(20)

    +Chiều thứ hai: số lượng người chơi trong trận đấu(8)

    +Chiều thứ ba: số sao của mỗi con tướng trong trận đấu

In [75]:
list_tiers = []

for player in range(len(all_players)):
    for match in range(len(all_players[0])):
        for each_player in range(8):
            temp = []
            player_champions = all_players[player][match]['info']['participants'][each_player]['units']
            for each_champion in range(len(player_champions)):     
                temp.append(all_players[player][match]['info']['participants'][each_player]['units'][each_champion]['tier'])      
            test1 = temp.copy()
            in_player.append(test1)
            temp.clear()
            
        test2 = in_player.copy()
        in_match.append(test2)
        in_player.clear()

    test3 = in_match.copy()
    list_tiers.append(test3)
    in_match.clear()

số sao của con tướng trong đội hình của từng người chơi trong trận đấu đầu tiên

In [77]:
list_tiers[0][0]

[[2, 3, 2, 3, 3, 3, 1],
 [2, 3, 2, 2, 2, 2, 2, 1],
 [2, 2, 3, 2, 2, 3, 2, 1],
 [2, 2, 2, 2, 2, 2, 2, 2],
 [2, 2, 2, 2, 2, 2, 2, 2],
 [2, 2, 1, 3, 1, 2, 2, 2],
 [2, 2, 3, 2, 2, 2, 2, 1],
 [2, 2, 1, 2, 2, 1, 1, 1]]

#### LẤY THỨ HẠNG CỦA TỪNG NGƯỜI CHƠI TRONG MỖI TRẬN ĐẤU

##### list_ranks: gồm 1 mảng 3 chiều: 

    +Chiều thứ nhất: gồm số lượng trận đấu người chơi(20)

    +Chiều thứ hai: gồm số người chơi trong trận

    +Chiều thứ ba: thứ hạng của người chơi

In [78]:
list_ranks = []
player_rank = []
in_match = []
for player in range(len(all_players)):
    for match in range(len(all_players[0])):
        for each_player in range(8):
            player_rank.append(all_players[player][match]['info']['participants'][each_player]['placement'])
        temp1 = player_rank.copy()
        in_match.append(temp1)
        player_rank.clear()
    temp2 = in_match.copy()
    list_ranks.append(temp2)
    in_match.clear()

top của trận đấu đầu tiên trong 20 trận đấu

In [87]:
list_ranks[0][0]

[1, 4, 7, 2, 5, 6, 3, 8]

### LƯU TẤT CẢ DỮ LIỆU VÀO DATAFRAME

##### tạo 1 dict để lưu trữ từng đội hình của từng trận đấu theo hàng:
    
+**Puuid**: Sử dụng hàm flatten để chuyển mảng 2 chiều thành mảng 1 chiều, sau đó ép vào cột đầu của dataframe

+**ID Match**: vì 1 trận đấu có 8 người chỉ tương đương với 1 ID Match nên ta sẽ phải lặp lại ID Match 8 lần để phù hợp với kích thước của dataframe


In [13]:
temp = {'Puuid': np.array(participants).flatten(), 
        'ID Match': np.array(np.array(id_match).repeat(8)).flatten(), 
        'Placement': np.array(list_ranks).flatten(),
        'List Augments': np.array(np.array(augments).flatten()),
        'List Traits': np.array(np.array(list_traits).flatten()),
        'List Champions': np.array(np.array(list_champions).flatten()),
        'List Number Items':np.array(np.array(list_items).flatten()),
        'List Champions Tier':(np.array(np.array(list_tiers).flatten())).flatten()}
process_data_tft_general = pd.DataFrame(temp)

In [14]:
process_data_tft_general.to_csv("process_data_tft_general_csv.csv")

### II) LẤY ĐỒ CỦA TỪNG TƯỚNG TRONG ĐỘI HÌNH CỦA NGƯỜI CHƠI

#### LẤY ĐỒ CỦA TỪNG TƯỚNG

##### list_items: 1 mảng 3 chiều:

    +Chiều thứ nhất: số lượng trận đấu(20)

    +Chiều thứ hai: số người chơi(8)

    +Chiều thứ ba: đồ của từng tướng trong đội hình của người chơi

In [88]:
list_items = []
in_match = []
in_player = []
for player in range(len(all_players)):
    for match in range(len((all_players[0]))):
        for each_player in range(8):
            items_champion = all_players[player][match]['info']['participants'][each_player]['units']
            temp = []
            for item in range(len(items_champion)):
                temp.append(all_players[player][match]['info']['participants'][each_player]['units'][item]['itemNames'])

            temp1 = temp.copy()
            in_match.append(temp1)
            temp.clear()

        temp2 = in_match.copy()
        in_player.append(temp2)
        in_match.clear()

    temp3 = in_player.copy()
    list_items.append(temp3)
    in_player.clear()  

món đồ của từng vị tướng trong đội hình của người chơi 1(trong 8) của trận đấu đầu tiên

In [92]:
list_items[0][0][0]

[['TFT_Item_ZekesHerald'],
 ['TFT_Item_BrambleVest', 'TFT_Item_TitansResolve', 'TFT_Item_DragonsClaw'],
 [],
 ['TFT_Item_DragonsClaw', 'TFT_Item_Bloodthirster'],
 ['TFT_Item_SpearOfShojin',
  'TFT_Item_ArchangelsStaff',
  'TFT_Item_HextechGunblade'],
 ['TFT_Item_SeraphsEmbrace',
  'TFT_Item_ArchangelsStaff',
  'TFT_Item_InfinityEdge'],
 []]

#### LẤY TÊN CỦA TƯỚNG

##### champions: 1 mảng 3 chiều:

    +Chiều thứ nhất: số trận đấu(20)

    +Chiều thứ hai: số lượng người chơi

    +Chiều thứ ba: 1 list tướng của người chơi đó

In [93]:
champions = []
in_match = []
in_player = []
for player in range(len(all_players)):
    for match in range(len(all_players[0])):
        for each_player in range(8):
            player_champions = all_players[player][match]['info']['participants'][each_player]['units']
            temp = []
            for name in range(len(player_champions)):
                temp.append(all_players[player][match]['info']['participants'][each_player]['units'][name]['character_id'])

            temp1 = temp.copy()
            in_match.append(temp1)
            temp.clear()

        temp2 = in_match.copy()
        in_player.append(temp2)
        in_match.clear()

    temp3 = in_player.copy()
    champions.append(temp3)
    in_player.clear() 

số tướng của người chơi thứ 1(trong 8) của trận đấu đầu tiên

In [96]:
champions[0][0][0]

['TFT8_Gangplank',
 'TFT8_Vi',
 'TFT8_LeeSin',
 'TFT8_Malphite',
 'TFT8_Ezreal',
 'TFT8_Sona',
 'TFT8_Kaisa']

In [17]:
temp = {'Puuid': np.array(participants).flatten(), 
        'ID Match': np.array(np.array(id_match).repeat(8)).flatten(), 
        'Champion': np.array(champions).flatten(),
        'List Name Item':np.array(list_items).flatten(),
        'Placement':np.array(list_ranks).flatten()}


process_data_tft_each_item = pd.DataFrame(temp)

In [97]:
process_data_tft_each_item["List Name Item"]

Series([], Name: List Name Item, dtype: float64)

In [19]:
# process_data_tft_each_item.to_csv("process_data_tft_each_item_csv.csv")